In [1]:
from src import API,Preprocessor
from src.preprocessing import remove_duplicates_Cleaner,moving_average_Filter,moving_max_Filter,moving_max_averaged_Filter,blank_Filter
import pandas as pd
from src.visualization import rssi_viewer
import os

from src.visualization import MapCreation
from src.DataLoader import MarkerLoader,gdfLoader



INFO - Logger configured


In [2]:
import ast
#API call
callApi=API()
# start="2023-07-12 11:03:00.000000"
# end="2023-07-12 12:04:00.000000"
# mac_module=os.environ['MAC_WEAR_DICT']['3480']
start="2023-07-18 09:12:00.000000"
end="2023-07-18 16:13:00.000000"
mac_module=ast.literal_eval(os.environ['MAC_WEAR_DICT'])['664E']


raw_data=callApi.getRawDataForCartoWear(mac_module,pd.to_datetime(start),pd.to_datetime(end))
print(raw_data)
#Preprocessing
sampling_time=2
window='10S'
preprocessor=Preprocessor(raw_data,sampling_time=sampling_time)
rssi_df=preprocessor.set_cleaner(remove_duplicates_Cleaner())\
        .cleaning()\
                .get_df()
rssi_df.to_csv('data/temp.csv')

INFO - data Cleaning


                   timestamp     macModule  rssi
0    2023-07-18 14:12:59.239  A8032A311F6A   -72
1    2023-07-18 14:12:56.516  A8032A311F6A   -73
2    2023-07-18 14:12:53.786  A8032A311F6A   -73
3    2023-07-18 14:12:51.439  A8032A311F96   -80
4    2023-07-18 14:12:50.862  A8032A311F6A   -73
...                      ...           ...   ...
7708 2023-07-18 07:58:23.556  A8032A312052   -79
7709 2023-07-18 07:58:22.077  A8032A311F6A   -65
7710 2023-07-18 07:58:19.732  A8032A311DAA   -70
7711 2023-07-18 07:58:19.399  A8032A311F6A   -72
7712 2023-07-18 07:58:11.633  A8032A311DAA   -79

[7713 rows x 3 columns]


In [3]:
fig=rssi_viewer(rssi_df)


In [4]:

ModuleMapPath="data/carteModulePalaiseau.csv"
marker_gdf=MarkerLoader(ModuleMapPath)
def getMacModuleLocation(marker_gdf):
    res={}
    for index,row in marker_gdf.iterrows():
        res[row['macModule']]=row['geometry']
    return res 
marker_location_dict=getMacModuleLocation(marker_gdf)


In [5]:

from timed_Folium.FeatureCreation.RawDataFeatures import RawDataFeatures
features=RawDataFeatures(rssi_df,marker_location_dict)
features

[{'type': 'Feature',
  'geometry': {'type': 'Point',
   'coordinates': [2.200638986440939, 48.71317445007082]},
  'properties': {'times': ['2023-07-18T14:12:59'],
   'icon': 'circle',
   'popup': '-72',
   'iconstyle': {'fillColor': '#009aff',
    'fillOpacity': '0.8',
    'radius': '28'}}},
 {'type': 'Feature',
  'geometry': {'type': 'Point',
   'coordinates': [2.200638986440939, 48.71317445007082]},
  'properties': {'times': ['2023-07-18T14:12:56'],
   'icon': 'circle',
   'popup': '-73',
   'iconstyle': {'fillColor': '#0077ff',
    'fillOpacity': '0.8',
    'radius': '27'}}},
 {'type': 'Feature',
  'geometry': {'type': 'Point',
   'coordinates': [2.200638986440939, 48.71317445007082]},
  'properties': {'times': ['2023-07-18T14:12:53'],
   'icon': 'circle',
   'popup': '-73',
   'iconstyle': {'fillColor': '#0077ff',
    'fillOpacity': '0.8',
    'radius': '27'}}},
 {'type': 'Feature',
  'geometry': {'type': 'Point',
   'coordinates': [2.2006869316821076, 48.71319455060883]},
  'prope

In [6]:
MapDataPath="data/cartePalaiseau.csv"
map_gdf=gdfLoader(MapDataPath)
m=MapCreation(map_gdf,marker_gdf=marker_gdf)
from folium.plugins import TimestampedGeoJson

MarkerLayer=TimestampedGeoJson(
                    {"type": "FeatureCollection","features": features},
                    period='PT2S',
                    duration='PT1S',
                    transition_time=sampling_time,
                    auto_play=True)
MarkerLayer.add_to(m)
m

In [7]:
def get_strongest_rssi(df,timestamp,timedelta,n):
    """
    Return the n strongest rssi values at a given timestamp
    """
    start=timestamp
    end=timestamp+pd.Timedelta(seconds=timedelta)
    return df.query('@start<=timestamp<@end').sort_values('rssi',ascending=False)['macModule'].head(n)

In [8]:
#ici on est obligé de passer de l'heure locale à l'heure UTC pour se raccorder à la bdd
import logging
logger = logging.getLogger('cartobat')

min_time=pd.to_datetime(start)-pd.Timedelta(hours=2)+pd.Timedelta(seconds=sampling_time)#permits to not have the issue of the starting data is incomplete
max_time=pd.to_datetime(end)-pd.Timedelta(hours=2)

time_range=pd.date_range(min_time,max_time,freq=pd.Timedelta(seconds=sampling_time))
number_of_mac_module=3


static_mac_module_list=get_strongest_rssi(rssi_df,min_time,sampling_time,number_of_mac_module).to_list()
print(static_mac_module_list)



[]


In [9]:

for i in time_range:
    current_strongest=get_strongest_rssi(rssi_df,i,sampling_time,number_of_mac_module).to_list()
    j=0
    
    while len(static_mac_module_list)<number_of_mac_module and j<len(current_strongest):
        mac_module=current_strongest[j]
        if mac_module not in static_mac_module_list:
            static_mac_module_list.append(mac_module)
        j+=1

    different_count=0
    for j in current_strongest:
        if j not in static_mac_module_list:
            different_count+=1

    if different_count>=2:
        print(str(i)+"movement detected")
        #reset the static_mac_module_list
        static_mac_module_list=current_strongest
    # elif different_count>=1:
    #     print(str(i)+"potential movement detected")

# transforming it in a function


2023-07-18 08:05:58movement detected
2023-07-18 14:12:36movement detected


In [10]:
def different_counter(static,current):
    '''The function `different_counter` counts the number of elements in the `current` list that are not present in the `static` list.

    Parameters
    ----------
    static
        A list or set of elements that represents the static or fixed elements.
    current
        A list of elements representing the current state or values.

    Returns
    -------
        the count of elements in the "current" list that are not present in the "static" list.

    '''
    different_count=0
    for k in current:
        if k not in static:
            different_count+=1
    return different_count
def static_mac_module_fill(current_strongest,static_mac_module_list):
    '''The function `static_mac_module_fill` takes a list of current strongest MAC modules and a list of static MAC modules, and adds MAC modules from the current strongest list to the static list until the static list has a length of 3 or all MAC modules from the current strongest list have been added.

    Parameters
    ----------
    current_strongest
        A list of current strongest MAC modules.
    static_mac_module_list
        A list that contains the static MAC modules. This list is initially empty and the function aims to fill it with MAC modules from the current_strongest list.

    Returns
    -------
        the updated static_mac_module_list.

    '''
    j=0
    while len(static_mac_module_list)<3 and j<len(current_strongest):
        mac_module=current_strongest[j]
        if mac_module not in static_mac_module_list:
            static_mac_module_list.append(mac_module)
        j+=1
    return static_mac_module_list
def detect_movement(rssi_df,time_range,sampling_time):
    '''The function `detect_movement` detects movement based on RSSI values in a given time range, with a threshold of 3 MAC modules and a reset after 20 seconds of static.

    Parameters
    ----------
    rssi_df
    time_range
        The `time_range` parameter is a pandas date range that specifies the range of time over which the movement detection should be performed. It is used to iterate through the specified time range and check for movement.
    sampling_time
        The sampling_time parameter represents the duration of each time interval in which the RSSI values are analyzed. It determines the granularity of the movement detection algorithm. For example, if sampling_time is set to 1 second, the algorithm will analyze the RSSI values every second to detect movement.
        
    Returns
    ----------
    res
        The `res` parameter is a list of timestamps at which movement was detected.
    '''
    
    
    #get min and max time from rssi_df
    min_time=rssi_df['timestamp'].min()
    max_time=rssi_df['timestamp'].max()
    time_range=pd.date_range(min_time,max_time,freq=pd.Timedelta(seconds=sampling_time))

    ##init
    last_movement_detected_strongest=get_strongest_rssi(rssi_df,min_time,sampling_time,3).to_list()
    static_mac_module_list=last_movement_detected_strongest
    last_detected=min_time
    static=False
    
    res=[]
    
    for i in time_range:
        
        current_strongest=get_strongest_rssi(rssi_df,i,sampling_time,3).to_list()

        #fill the static_mac_module_list when it is not full
        static_mac_module_list=static_mac_module_fill(current_strongest,static_mac_module_list)
            
        original_difference_count=different_counter(last_movement_detected_strongest,current_strongest)
        different_count=different_counter(static_mac_module_list,current_strongest)
        if different_count>=2 or original_difference_count >=3:
            print(str(i)+"movement detected")
            res.append(i)
            #reset the static_mac_module_list
            static_mac_module_list=current_strongest
            last_movement_detected_strongest=current_strongest
            last_detected=i
            static=False
        # if last movement detected was more than 20 seconds ago
        if static== False and i>last_detected+pd.Timedelta(seconds=20):
            static_mac_module_list=current_strongest
            static=True 
    return res

In [11]:
detect_movement(rssi_df,time_range,sampling_time)

2023-07-18 14:12:31.633000movement detected
2023-07-18 14:12:35.633000movement detected


[Timestamp('2023-07-18 14:12:31.633000'),
 Timestamp('2023-07-18 14:12:35.633000')]